<a href="https://www.kaggle.com/code/princeiornongu/climate-change-time-series-predicting-the-stc?scriptVersionId=164894752" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

#### Essential Libraries

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

import warnings
warnings.filterwarnings('ignore')

In [2]:
pip install pycountry

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.2/6.2 MB 45.6 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


In [3]:
import pycountry

# Fetch ISO3 country codes
valid_iso3_codes = [country.alpha_3 for country in pycountry.countries]

# Convert to set for faster lookup
valid_iso3_set = set(valid_iso3_codes)

#### Importing Datasets and Feature Engineering

In [4]:
df = pd.read_csv("/kaggle/input/climate-change-indicators/climate_change_indicators.csv")
df

ObjectId                       Country ISO2 ISO3  \
0           1  Afghanistan, Islamic Rep. of   AF  AFG   
1           2                       Albania   AL  ALB   
2           3                       Algeria   DZ  DZA   
3           4                American Samoa   AS  ASM   
4           5      Andorra, Principality of   AD  AND   
..        ...                           ...  ...  ...   
220       221                Western Sahara   EH  ESH   
221       222                         World  NaN  WLD   
222       223                Yemen, Rep. of   YE  YEM   
223       224                        Zambia   ZM  ZMB   
224       225                      Zimbabwe   ZW  ZWE   

                                             Indicator            Unit  \
0    Temperature change with respect to a baseline ...  Degree Celsius   
1    Temperature change with respect to a baseline ...  Degree Celsius   
2    Temperature change with respect to a baseline ...  Degree Celsius   
3    Temperature change with respect to a baseline ...  Degree Celsius   
4    Temperature change with respect to a baseline ...  Degree Celsius   
..                                                 ...             ...   
220  Temperature change with respect to a baseline ...  Degree Celsius   
221  Temperature change with respect to a baseline ...  Degree Celsius   
222  Temperature change with respect to a baseline ...  Degree Celsius   
223  Temperature change with respect to a baseline ...  Degree Celsius   
224  Temperature change with respect to a baseline ...  Degree Celsius   

                                                Source CTS_Code  \
0    Food and Agriculture Organization of the Unite...     ECCS   
1    Food and Agriculture Organization of the Unite...     ECCS   
2    Food and Agriculture Organization of the Unite...     ECCS   
3    Food and Agriculture Organization of the Unite...     ECCS   
4    Food and Agriculture Organization of the Unite...     ECCS   
..                                                 ...      ...   
220  Food and Agriculture Organization of the Unite...     ECCS   
221  Food and Agriculture Organization of the Unite...     ECCS   
222  Food and Agriculture Organization of the Unite...     ECCS   
223  Food and Agriculture Organization of the Unite...     ECCS   
224  Food and Agriculture Organization of the Unite...     ECCS   

                       CTS_Name  \
0    Surface Temperature Change   
1    Surface Temperature Change   
2    Surface Temperature Change   
3    Surface Temperature Change   
4    Surface Temperature Change   
..                          ...   
220  Surface Temperature Change   
221  Surface Temperature Change   
222  Surface Temperature Change   
223  Surface Temperature Change   
224  Surface Temperature Change   

                                   CTS_Full_Descriptor  ...  F2013  F2014  \
0    Environment, Climate Change, Climate Indicator...  ...  1.281  0.456   
1    Environment, Climate Change, Climate Indicator...  ...  1.333  1.198   
2    Environment, Climate Change, Climate Indicator...  ...  1.192  1.690   
3    Environment, Climate Change, Climate Indicator...  ...  1.257  1.170   
4    Environment, Climate Change, Climate Indicator...  ...  0.831  1.946   
..                                                 ...  ...    ...    ...   
220  Environment, Climate Change, Climate Indicator...  ...  1.423  1.401   
221  Environment, Climate Change, Climate Indicator...  ...  1.016  1.053   
222  Environment, Climate Change, Climate Indicator...  ...    NaN    NaN   
223  Environment, Climate Change, Climate Indicator...  ...  0.790  0.917   
224  Environment, Climate Change, Climate Indicator...  ...  0.118  0.025   

     F2015  F2016  F2017  F2018  F2019  F2020  F2021  F2022  
0    1.093  1.555  1.540  1.544  0.910  0.498  1.327  2.012  
1    1.569  1.464  1.121  2.028  1.675  1.498  1.536  1.518  
2    1.121  1.757  1.512  1.210  1.115  1.926  2.330  1.688  
3    1.009  1.539  1.435  1.189 

In [5]:
df1 = df.copy()
df1.drop(['ObjectId', 'ISO2', 'CTS_Code', 'CTS_Name', 'CTS_Full_Descriptor', ], axis=1, inplace=True)
df1.columns = df1.columns.str.replace('F', '')
df1 = df1[df1['ISO3'].isin(valid_iso3_set)]
df1

Country ISO3  \
0    Afghanistan, Islamic Rep. of  AFG   
1                         Albania  ALB   
2                         Algeria  DZA   
3                  American Samoa  ASM   
4        Andorra, Principality of  AND   
..                            ...  ...   
219            West Bank and Gaza  PSE   
220                Western Sahara  ESH   
222                Yemen, Rep. of  YEM   
223                        Zambia  ZMB   
224                      Zimbabwe  ZWE   

                                             Indicator            Unit  \
0    Temperature change with respect to a baseline ...  Degree Celsius   
1    Temperature change with respect to a baseline ...  Degree Celsius   
2    Temperature change with respect to a baseline ...  Degree Celsius   
3    Temperature change with respect to a baseline ...  Degree Celsius   
4    Temperature change with respect to a baseline ...  Degree Celsius   
..                                                 ...             ...   
219  Temperature change with respect to a baseline ...  Degree Celsius   
220  Temperature change with respect to a baseline ...  Degree Celsius   
222  Temperature change with respect to a baseline ...  Degree Celsius   
223  Temperature change with respect to a baseline ...  Degree Celsius   
224  Temperature change with respect to a baseline ...  Degree Celsius   

                                                Source   1961   1962   1963  \
0    Food and Agriculture Organization of the Unite... -0.113 -0.164  0.847   
1    Food and Agriculture Organization of the Unite...  0.627  0.326  0.075   
2    Food and Agriculture Organization of the Unite...  0.164  0.114  0.077   
3    Food and Agriculture Organization of the Unite...  0.079 -0.042  0.169   
4    Food and Agriculture Organization of the Unite...  0.736  0.112 -0.752   
..                                                 ...    ...    ...    ...   
219  Food and Agriculture Organization of the Unite... -0.110  0.822  0.848   
220  Food and Agriculture Organization of the Unite...  0.632  0.576  0.333   
222  Food and Agriculture Organization of the Unite...  0.029 -0.009  0.169   
223  Food and Agriculture Organization of the Unite...  0.228 -0.168 -0.390   
224  Food and Agriculture Organization of the Unite...  0.267  0.237 -0.458   

      1964   1965  ...   2013   2014   2015   2016   2017   2018   2019  \
0   -0.764 -0.244  ...  1.281  0.456  1.093  1.555  1.540  1.544  0.910   
1   -0.166 -0.388  ...  1.333  1.198  1.569  1.464  1.121  2.028  1.675   
2    0.250 -0.100  ...  1.192  1.690  1.121  1.757  1.512  1.210  1.115   
3   -0.140 -0.562  ...  1.257  1.170  1.009  1.539  1.435  1.189  1.539   
4    0.308 -0.490  ...  0.831  1.946  1.690  1.990  1.925  1.919  1.964   
..     ...    ...  ...    ...    ...    ...    ...    ...    ...    ...   
219 -0.626 -0.031  ...  1.114  0.863  1.326  1.615  0.735  2.007  1.204   
220  0.819 -0.337  ...  1.423  1.401  1.510  1.732  2.204  0.942  1.477   
222 -0.251 -0.623  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
223 -0.279 -0.418  ...  0.790  0.917  1.450  1.401  0.105  0.648  0.855   
224 -0.097 -0.480  ...  0.118  0.025  0.970  1.270  0.088  0.453  0.925   

      2020   2021   2022  
0    0.498  1.327  2.012  
1    1.498  1.536  1.518  
2    1.926  2.330  1.688  
3    1.430  1.268  1.256  
4    2.562  1.533  3.243  
..     ...    ...    ...  
219  1.455  1.787  1.074  
220  2.069  1.593  1.970  
222    NaN    NaN    NaN  
223  0.891  0.822  0.686  
224  0.389 -0.125 -0.490  

[224 rows x 67 columns]

In [6]:
# Loop through each column and fill missing values with the mean if the column contains numeric data
for column in df1.columns:
    if df1[column].dtype in ['int64', 'float64']:
        df1[column].fillna(df1[column].mean(), inplace=True)

In [7]:
df1.describe()

1961        1962        1963        1964        1965        1966  \
count  224.000000  224.000000  224.000000  224.000000  224.000000  224.000000   
mean     0.162797   -0.013750   -0.006973   -0.069118   -0.247155    0.105005   
std      0.370930    0.313825    0.354514    0.282994    0.247915    0.350162   
min     -0.694000   -0.908000   -1.270000   -0.877000   -1.064000   -1.801000   
25%     -0.067250   -0.146000   -0.166000   -0.212250   -0.362750   -0.007750   
50%      0.146000   -0.025000   -0.006973   -0.069118   -0.247155    0.105005   
75%      0.252750    0.082000    0.173000    0.098250   -0.110000    0.238250   
max      1.892000    0.998000    1.202000    1.097000    0.857000    1.151000   

            1967        1968        1969        1970  ...        2013  \
count  224.00000  224.000000  224.000000  224.000000  ...  224.000000   
mean    -0.11080   -0.199495    0.159265    0.092181  ...    0.930805   
std      0.31336    0.249296    0.283550    0.323241  ...    0.315722   
min     -1.04800   -1.634000   -0.900000   -1.288000  ...    0.118000   
25%     -0.25200   -0.287250    0.024000   -0.021000  ...    0.749000   
50%     -0.11080   -0.199495    0.159265    0.092181  ...    0.919000   
75%     -0.04000   -0.093500    0.304750    0.248250  ...    1.182250   
max      1.13400    0.476000    0.939000    0.978000  ...    1.643000   

             2014        2015        2016        2017        2018        2019  \
count  224.000000  224.000000  224.000000  224.000000  224.000000  224.000000   
mean     1.115102    1.269112    1.438481    1.280089    1.302170    1.443057   
std      0.554662    0.453696    0.390793    0.384935    0.581881    0.455834   
min     -0.092000   -0.430000    0.250000    0.017000    0.238000    0.050000   
25%      0.758250    1.031500    1.163500    1.038500    0.880250    1.174250   
50%      1.008000    1.231500    1.438481    1.280089    1.148500    1.432500   
75%      1.310000    1.516000    1.692750    1.514500    1.621750    1.676000   
max      2.704000    2.613000    2.459000    2.493000    2.772000    2.689000   

             2020        2021        2022  
count  224.000000  224.000000  224.000000  
mean     1.551284    1.343042    1.382057  
std      0.604871    0.472536    0.652563  
min      0.229000   -0.425000   -1.305000  
25%      1.182250    1.028250    0.892250  
50%      1.493000    1.343042    1.340500  
75%      1.779250    1.596500    1.875250  
max      3.691000    2.676000    3.243000  

[8 rows x 62 columns]

In [8]:
df3 = pd.read_csv("/kaggle/input/mapping-of-features-world-pop/Metadata_Country_API_NY.GDP.MKTP.CD_DS2_en_csv_v2_6298258.csv")
df3.rename(columns={"TableName": "Country", "Region": "Sub-Region", "IncomeGroup": "Income Group"}, inplace =True)
df3.drop(columns=['Unnamed: 5', 'SpecialNotes', 'Country Code'], inplace=True)

In [9]:
df4= pd.read_csv('/kaggle/input/world-population-statistics-2023/world_population_data.csv')
columns_to_drop = ['rank', 'cca3', '2022 population', '2020 population',	'2015 population', '2010 population',	'2000 population',	'1990 population',	'1980 population',
                   '1970 population', '2023 population', 'growth rate', 'world percentage', 'continent']
df4.drop(columns_to_drop, axis=1, inplace=True)
df4.rename(columns={"country": "Country", "area (km²)": "Area (KM²)", "density (km²)": "Density (KM²)"}, inplace =True)
df4

Country  Area (KM²)  Density (KM²)
0               India  3287590.00            481
1               China  9706961.00            151
2       United States  9372610.00             37
3           Indonesia  1904569.00            148
4            Pakistan   881912.00            312
..                ...         ...            ...
229        Montserrat      102.00             43
230  Falkland Islands    12173.00              0
231              Niue      261.00              7
232           Tokelau       12.00            189
233      Vatican City        0.44           1177

[234 rows x 3 columns]

In [10]:
df5=pd.read_csv('/kaggle/input/melted-world-population/mpopC.csv')
df5.dropna(subset=['Population Size in Y'], inplace=True)
df5['Population Size in Y'] = df5['Population Size in Y'].astype(int)
df5['Year'] = pd.to_numeric(df5['Year'])
df5

Country Country Code  Year  Population Size in Y
0                            Aruba          ABW  1961                 55811
1      Africa Eastern and Southern          AFE  1961             134169237
2                      Afghanistan          AFG  1961               8790140
3       Africa Western and Central          AFW  1961              99314028
4                           Angola          AGO  1961               5441333
...                            ...          ...   ...                   ...
16487                       Kosovo          XKX  2022               1761985
16488                  Yemen, Rep.          YEM  2022              33696614
16489                 South Africa          ZAF  2022              59893885
16490                       Zambia          ZMB  2022              20017675
16491                     Zimbabwe          ZWE  2022              16320537

[16492 rows x 4 columns]

In [11]:
# Perform inner join based on the "Country" column
merged_data = pd.merge(df1, df3, on="Country").merge(df4, on="Country")
# Save the merged data into a new CSV file
#merged_data= pd.read_csv("/kaggle/input/merged-cc/CC.csv")

In [12]:
f1 = pd.read_csv("/kaggle/input/merged-cc/CC.csv")
f1 = f1.reindex(columns=['Country', 'ISO3','Sub-Region', 'Area (KM²)',	'Density (KM²)', 'Income Group',
                                       '1961', '1962','1963', '1964', '1965', '1966', '1967', '1968', '1969', '1970', '1971',
                                        '1972', '1973', '1974', '1975', '1976', '1977', '1978', '1979', '1980',
                                        '1981', '1982', '1983', '1984', '1985', '1986', '1987', '1988', '1989',
                                        '1990', '1991', '1992', '1993', '1994', '1995', '1996', '1997', '1998',
                                        '1999', '2000', '2001', '2002', '2003', '2004', '2005', '2006', '2007',
                                        '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016',
                                        '2017', '2018', '2019', '2020', '2021', '2022',
                                        'Indicator', 'Unit', 'Source'])# final
f1

Country ISO3                  Sub-Region  Area (KM²)  \
0                Albania  ALB       Europe & Central Asia     28748.0   
1                Algeria  DZA  Middle East & North Africa   2381741.0   
2         American Samoa  ASM         East Asia & Pacific       199.0   
3                 Angola  AGO          Sub-Saharan Africa   1246700.0   
4    Antigua and Barbuda  ATG   Latin America & Caribbean       442.0   
..                   ...  ...                         ...         ...   
136        United States  USA               North America   9372610.0   
137              Uruguay  URY   Latin America & Caribbean    181034.0   
138              Vanuatu  VUT         East Asia & Pacific     12189.0   
139               Zambia  ZMB          Sub-Saharan Africa    752612.0   
140             Zimbabwe  ZWE          Sub-Saharan Africa    390757.0   

     Density (KM²)         Income Group   1961   1962   1963   1964  ...  \
0              103  Upper middle income  0.627  0.326  0.075 -0.166  ...   
1               19  Lower middle income  0.164  0.114  0.077  0.250  ...   
2              220          High income  0.079 -0.042  0.169 -0.140  ...   
3               29  Lower middle income  0.041 -0.152 -0.190 -0.229  ...   
4              214          High income  0.090  0.031  0.288  0.214  ...   
..             ...                  ...    ...    ...    ...    ...  ...   
136             37          High income  0.003 -0.026  0.418 -0.282  ...   
137             20          High income  0.398 -0.473  0.330 -0.762  ...   
138             27  Lower middle income  0.168  0.092 -0.165  0.220  ...   
139             28  Lower middle income  0.228 -0.168 -0.390 -0.279  ...   
140             43  Lower middle income  0.267  0.237 -0.458 -0.097  ...   

      2016   2017   2018   2019   2020   2021   2022  \
0    1.464  1.121  2.028  1.675  1.498  1.536  1.518   
1    1.757  1.512  1.210  1.115  1.926  2.330  1.688   
2    1.539  1.435  1.189  1.539  1.430  1.268  1.256   
3    1.609  0.870  1.395  1.752  1.162  1.553  1.212   
4    1.097  0.958  0.627  0.797  1.131  0.862  0.770   
..     ...    ...    ...    ...    ...    ...    ...   
136  2.224  1.433  1.276  1.034  1.324  1.144  1.217   
137  0.301  1.546  1.196  0.766  0.890  0.790  0.382   
138  1.146  1.131  0.613  0.897  1.226  1.147  1.479   
139  1.401  0.105  0.648  0.855  0.891  0.822  0.686   
140  1.270  0.088  0.453  0.925  0.389 -0.125 -0.490   

                                             Indicator            Unit  \
0    Temperature change with respect to a baseline ...  Degree Celsius   
1    Temperature change with respect to a baseline ...  Degree Celsius   
2    Temperature change with respect to a baseline ...  Degree Celsius   
3    Temperature change with respect to a baseline ...  Degree Celsius   
4    Temperature change with respect to a baseline ...  Degree Celsius   
..                                                 ...             ...   
136  Temperature change with respect to a baseline ...  Degree Celsius   
137  Temperature change with respect to a baseline ...  Degree Celsius   
138  Temperature change with respect to a baseline ...  Degree Celsius   
139  Temperature change with respect to a baseline ...  Degree Celsius   
140  Temperature change with respect to a baseline ...  Degree Celsius   

                                                Source  
0    Food and Agriculture Organization of the Unite...  
1    Food and Agriculture Organization of the Unite...  
2    Food and Agriculture Organization of the Unite...  
3    Food and Agriculture Organization of the Unite...  
4    Food and Agriculture Organization of the Unite...  
..                                                 ...  
136  Food and Agriculture Organization of the Unite...  
137  Food and Agriculture Organization of the Unite...  
138  Food and Agriculture Organization of the Unite...  
139  Food and Agriculture Organization of the Unite...  
140  Food and Agriculture Organization

#### Melting Dataset

In [13]:
f2= f1.copy()
# Identify columns to keep as identifiers (e.g., Country Name, Country Code, Region, IncomeGroup)
id_cols = ['Country', 'ISO3', 'Sub-Region', 'Income Group', 'Indicator', 'Unit', 'Source',
                                      'Area (KM²)',	'Density (KM²)',]
f2 = pd.melt(f2, id_vars=id_cols, var_name='Year', value_name='Surface Temperature Change')
f2['Year'] = pd.to_numeric(f2['Year'])
f2

Country ISO3                  Sub-Region  \
0                 Albania  ALB       Europe & Central Asia   
1                 Algeria  DZA  Middle East & North Africa   
2          American Samoa  ASM         East Asia & Pacific   
3                  Angola  AGO          Sub-Saharan Africa   
4     Antigua and Barbuda  ATG   Latin America & Caribbean   
...                   ...  ...                         ...   
8737        United States  USA               North America   
8738              Uruguay  URY   Latin America & Caribbean   
8739              Vanuatu  VUT         East Asia & Pacific   
8740               Zambia  ZMB          Sub-Saharan Africa   
8741             Zimbabwe  ZWE          Sub-Saharan Africa   

             Income Group                                          Indicator  \
0     Upper middle income  Temperature change with respect to a baseline ...   
1     Lower middle income  Temperature change with respect to a baseline ...   
2             High income  Temperature change with respect to a baseline ...   
3     Lower middle income  Temperature change with respect to a baseline ...   
4             High income  Temperature change with respect to a baseline ...   
...                   ...                                                ...   
8737          High income  Temperature change with respect to a baseline ...   
8738          High income  Temperature change with respect to a baseline ...   
8739  Lower middle income  Temperature change with respect to a baseline ...   
8740  Lower middle income  Temperature change with respect to a baseline ...   
8741  Lower middle income  Temperature change with respect to a baseline ...   

                Unit                                             Source  \
0     Degree Celsius  Food and Agriculture Organization of the Unite...   
1     Degree Celsius  Food and Agriculture Organization of the Unite...   
2     Degree Celsius  Food and Agriculture Organization of the Unite...   
3     Degree Celsius  Food and Agriculture Organization of the Unite...   
4     Degree Celsius  Food and Agriculture Organization of the Unite...   
...              ...                                                ...   
8737  Degree Celsius  Food and Agriculture Organization of the Unite...   
8738  Degree Celsius  Food and Agriculture Organization of the Unite...   
8739  Degree Celsius  Food and Agriculture Organization of the Unite...   
8740  Degree Celsius  Food and Agriculture Organization of the Unite...   
8741  Degree Celsius  Food and Agriculture Organization of the Unite...   

      Area (KM²)  Density (KM²)  Year  Surface Temperature Change  
0        28748.0            103  1961                       0.627  
1      2381741.0             19  1961                       0.164  
2          199.0            220  1961                       0.079  
3      1246700.0             29  1961                       0.041  
4          442.0            214  1961                       0.090  
...          ...            ...   ...                         ...  
8737   9372610.0             37  2022                       1.217  
8738    181034.0             20  2022                       0.382  
8739     12189.0             27  2022                       1.479  
8740    752612.0             28  2022                       0.686  
8741    390757.0             43  2022                      -0.490  

[8742 rows x 11 columns]

In [14]:
dfi = pd.merge(f2, df5, on=["Country", "Year"])
dfi = dfi.drop('Country Code', axis=1)

In [15]:
dfi

Country ISO3                  Sub-Region  \
0                 Albania  ALB       Europe & Central Asia   
1                 Algeria  DZA  Middle East & North Africa   
2          American Samoa  ASM         East Asia & Pacific   
3                  Angola  AGO          Sub-Saharan Africa   
4     Antigua and Barbuda  ATG   Latin America & Caribbean   
...                   ...  ...                         ...   
8737        United States  USA               North America   
8738              Uruguay  URY   Latin America & Caribbean   
8739              Vanuatu  VUT         East Asia & Pacific   
8740               Zambia  ZMB          Sub-Saharan Africa   
8741             Zimbabwe  ZWE          Sub-Saharan Africa   

             Income Group                                          Indicator  \
0     Upper middle income  Temperature change with respect to a baseline ...   
1     Lower middle income  Temperature change with respect to a baseline ...   
2             High income  Temperature change with respect to a baseline ...   
3     Lower middle income  Temperature change with respect to a baseline ...   
4             High income  Temperature change with respect to a baseline ...   
...                   ...                                                ...   
8737          High income  Temperature change with respect to a baseline ...   
8738          High income  Temperature change with respect to a baseline ...   
8739  Lower middle income  Temperature change with respect to a baseline ...   
8740  Lower middle income  Temperature change with respect to a baseline ...   
8741  Lower middle income  Temperature change with respect to a baseline ...   

                Unit                                             Source  \
0     Degree Celsius  Food and Agriculture Organization of the Unite...   
1     Degree Celsius  Food and Agriculture Organization of the Unite...   
2     Degree Celsius  Food and Agriculture Organization of the Unite...   
3     Degree Celsius  Food and Agriculture Organization of the Unite...   
4     Degree Celsius  Food and Agriculture Organization of the Unite...   
...              ...                                                ...   
8737  Degree Celsius  Food and Agriculture Organization of the Unite...   
8738  Degree Celsius  Food and Agriculture Organization of the Unite...   
8739  Degree Celsius  Food and Agriculture Organization of the Unite...   
8740  Degree Celsius  Food and Agriculture Organization of the Unite...   
8741  Degree Celsius  Food and Agriculture Organization of the Unite...   

      Area (KM²)  Density (KM²)  Year  Surface Temperature Change  \
0        28748.0            103  1961                       0.627   
1      2381741.0             19  1961                       0.164   
2          199.0            220  1961                       0.079   
3      1246700.0             29  1961                       0.041   
4          442.0            214  1961                       0.090   
...          ...            ...   ...                         ...   
8737   9372610.0             37  2022                       1.217   
8738    181034.0             20  2022                       0.382   
8739     12189.0             27  2022                       1.479   
8740    752612.0             28  2022                       0.686   
8741    390757.0             43  2022                      -0.490   

      Population Size in Y  
0                  1659800  
1                 11598608  
2                    20626  
3                  5441333  
4                    56245  
...                    ...  
8737             333287557  
8738               3422794  
8739                326740  
8740              20017675  
8741              16320537  

[8742 rows x 12 columns]

In [16]:
dfi[dfi['Country'] == 'India'] # check if the code work by highlighting a specific country

Country ISO3  Sub-Region         Income Group  \
57     India  IND  South Asia  Lower middle income   
198    India  IND  South Asia  Lower middle income   
339    India  IND  South Asia  Lower middle income   
480    India  IND  South Asia  Lower middle income   
621    India  IND  South Asia  Lower middle income   
...      ...  ...         ...                  ...   
8094   India  IND  South Asia  Lower middle income   
8235   India  IND  South Asia  Lower middle income   
8376   India  IND  South Asia  Lower middle income   
8517   India  IND  South Asia  Lower middle income   
8658   India  IND  South Asia  Lower middle income   

                                              Indicator            Unit  \
57    Temperature change with respect to a baseline ...  Degree Celsius   
198   Temperature change with respect to a baseline ...  Degree Celsius   
339   Temperature change with respect to a baseline ...  Degree Celsius   
480   Temperature change with respect to a baseline ...  Degree Celsius   
621   Temperature change with respect to a baseline ...  Degree Celsius   
...                                                 ...             ...   
8094  Temperature change with respect to a baseline ...  Degree Celsius   
8235  Temperature change with respect to a baseline ...  Degree Celsius   
8376  Temperature change with respect to a baseline ...  Degree Celsius   
8517  Temperature change with respect to a baseline ...  Degree Celsius   
8658  Temperature change with respect to a baseline ...  Degree Celsius   

                                                 Source  Area (KM²)  \
57    Food and Agriculture Organization of the Unite...   3287590.0   
198   Food and Agriculture Organization of the Unite...   3287590.0   
339   Food and Agriculture Organization of the Unite...   3287590.0   
480   Food and Agriculture Organization of the Unite...   3287590.0   
621   Food and Agriculture Organization of the Unite...   3287590.0   
...                                                 ...         ...   
8094  Food and Agriculture Organization of the Unite...   3287590.0   
8235  Food and Agriculture Organization of the Unite...   3287590.0   
8376  Food and Agriculture Organization of the Unite...   3287590.0   
8517  Food and Agriculture Organization of the Unite...   3287590.0   
8658  Food and Agriculture Organization of the Unite...   3287590.0   

      Density (KM²)  Year  Surface Temperature Change  Population Size in Y  
57              481  1961                      -0.208             456351876  
198             481  1962                      -0.479             467024193  
339             481  1963                      -0.030             477933619  
480             481  1964                      -0.030             489059309  
621             481  1965                      -0.072             500114346  
...             ...   ...                         ...                   ...  
8094            481  2018                       0.874            1369003306  
8235            481  2019                       0.802            1383112050  
8376            481  2020                       0.520            1396387127  
8517            481  2021                       0.733            1407563842  
8658            481  2022                       0.790            1417173173  

[62 rows x 12 columns]

#### Exploring Dataset

In [17]:
dfi.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8742 entries, 0 to 8741
Data columns (total 12 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   Country                     8742 non-null   object 
 1   ISO3                        8742 non-null   object 
 2   Sub-Region                  8742 non-null   object 
 3   Income Group                8742 non-null   object 
 4   Indicator                   8742 non-null   object 
 5   Unit                        8742 non-null   object 
 6   Source                      8742 non-null   object 
 7   Area (KM²)                  8742 non-null   float64
 8   Density (KM²)               8742 non-null   int64  
 9   Year                        8742 non-null   int64  
 10  Surface Temperature Change  8742 non-null   float64
 11  Population Size in Y        8742 non-null   int64  
dtypes: float64(2), int64(3), object(7)
memory usage: 819.7+ KB


In [18]:
dfi.isnull().sum()

Country                       0
ISO3                          0
Sub-Region                    0
Income Group                  0
Indicator                     0
Unit                          0
Source                        0
Area (KM²)                    0
Density (KM²)                 0
Year                          0
Surface Temperature Change    0
Population Size in Y          0
dtype: int64

In [19]:
dfi.describe()

Area (KM²)  Density (KM²)         Year  Surface Temperature Change  \
count  8.742000e+03    8742.000000  8742.000000                 8742.000000   
mean   6.291204e+05     384.517730  1991.500000                    0.512356   
std    1.542088e+06    1714.786413    17.896554                    0.635500   
min    2.020000e+00       0.000000  1961.000000                   -2.062000   
25%    2.104100e+04      27.000000  1976.000000                    0.062000   
50%    1.184840e+05      92.000000  1991.500000                    0.441500   
75%    4.881000e+05     223.000000  2007.000000                    0.921000   
max    9.984670e+06   18149.000000  2022.000000                    3.550000   

       Population Size in Y  
count          8.742000e+03  
mean           2.430457e+07  
std            8.806501e+07  
min            5.436000e+03  
25%            7.666828e+05  
50%            4.919355e+06  
75%            1.474949e+07  
max            1.417173e+09

#### EDA

In [20]:
# Create animated choropleth map
fig = px.choropleth(dfi,
                    locations="ISO3",
                    color="Surface Temperature Change",
                    hover_name="Country",
                    animation_frame="Year",
                    title="Annual Surface Temperature Change",
                    color_continuous_scale=px.colors.sequential.Plasma)

# Add titles and labels
fig.update_layout(geo=dict(showcoastlines=True),
                  coloraxis_colorbar=dict(title="Surface Temp Change"))

# Show the plot
fig.show()

In [21]:
# Time Series Plot by Sub-Region
fig1 = px.line(dfi, x="Year", y="Surface Temperature Change",
               title="Surface Temperature Change Over Time by Sub-Region",
               color="Sub-Region",
               labels={"Surface Temperature Change": "Temperature Change (°C)"})

# Show the plot
fig1.show()

In [22]:
# Create line chart
fig2 = px.line(dfi, x='Year', y='Population Size in Y', color = "Country",
              title='Population Size Over Time by Country')

# Show the plot
fig2.show()

In [23]:
# Time Series Plot by Sub-Region
fig3 = px.line(dfi, x="Year", y="Surface Temperature Change",
               title="Surface Temperature Change Over Time by Income Group",
               color="Income Group",
               labels={"Surface Temperature Change": "Temperature Change (°C)"})

# Show the plot
fig3.show()

In [24]:
# Time Series Plot by Sub-Region
figx = px.line(dfi, x="Year", y="Surface Temperature Change",
               title="Surface Temperature Change Over Time by Income Group",
               color="Country",
               labels={"Surface Temperature Change": "Temperature Change (°C)"})

# Show the plot
figx.show()

In [25]:
# Pie Chart
subregion_pie = dfi.groupby("Sub-Region")["Surface Temperature Change"].sum()
fig4 = px.pie(values=subregion_pie.values, names=subregion_pie.index, title="Surface Temperature Change by Sub-Region")
fig4.show()

In [26]:
# Pie Chart
incomegroup_pie = f2.groupby("Income Group")["Surface Temperature Change"].sum()
fig5 = px.pie(values=incomegroup_pie.values, names=incomegroup_pie.index, title="Surface Temperature Change by Sub-Region")
fig5.show()

In [27]:
# Scatter plot: Surface Temperature Change vs. Area with country names
fig6 = px.scatter(dfi, x='Area (KM²)', y='Surface Temperature Change', hover_data=['Country','Year'],
                  title='Surface Temperature Change vs. Area', color='Area (KM²)',
                  labels={'Surface Temperature Change': 'Temperature Change (°C)', 'Area (KM²)': 'Area (km²)'})
fig6.show()

In [28]:
# Scatter plot: Surface Temperature Change vs. Area with country names
fig7 = px.scatter(f2, x='Density (KM²)', y='Surface Temperature Change', hover_data=['Country','Year'],
                  title='Surface Temperature Change vs. Density', color='Density (KM²)',
                  labels={'Surface Temperature Change': 'Temperature Change (°C)', 'Density (KM²)': 'Density (km²)'})
fig7.show()

In [29]:
# Line Chart - Surface Temperature Change over the Years
fig8 = px.line(dfi, x='Year', y='Surface Temperature Change', title='Surface Temperature Change over the Years')
fig8.show()

In [30]:
# Bubble Chart - Population Size vs Surface Temperature Change
fig9 = px.scatter(dfi, x='Population Size in Y', y='Surface Temperature Change',
                 size='Area (KM²)', color='Income Group', hover_name='Country',
                 title='Population Size vs Surface Temperature Change',
                 labels={'Population Size in Y': 'Population Size', 'Surface Temperature Change': 'Surface Temp Change'})
fig9.show()

In [31]:
# Bar chart of Sub-Region with Average Density
avg_density = dfi.groupby('Sub-Region')['Density (KM²)'].mean().reset_index()
figxi = px.bar(avg_density, x='Sub-Region', y='Density (KM²)', title='Average Density by Sub-Region')
figxi.show()

In [32]:
# Heatmap of Correlation
#correlation_matrix = dfi.corr()
#figxii = px.imshow(correlation_matrix, color_continuous_scale='Viridis',
                 #labels=dict(x="Features", y="Features", color="Correlation"),
                 #title='Correlation Matrix')
#figxii.show()

In [33]:
figxiii = px.scatter_matrix(dfi, dimensions=['Country', 'Area (KM²)', 'Density (KM²)', 'Population Size in Y', 'Surface Temperature Change'], color='Country')
figxiii.show()

#### Time Series

In [34]:
tsdf = dfi.copy()

In [35]:
# Convert the 'Year' column to datetime format
tsdf['Year'] = pd.to_datetime(tsdf['Year'], format='%Y')
tsdf.set_index('Year', inplace=True)

In [36]:
# Group the data by country
grouped = tsdf.groupby('Country')

In [37]:
# Assuming 'STC' is the column you want to forecast
tsd = tsdf[['Surface Temperature Change', 'Country']]
tsd

Surface Temperature Change              Country
Year                                                       
1961-01-01                       0.627              Albania
1961-01-01                       0.164              Algeria
1961-01-01                       0.079       American Samoa
1961-01-01                       0.041               Angola
1961-01-01                       0.090  Antigua and Barbuda
...                                ...                  ...
2022-01-01                       1.217        United States
2022-01-01                       0.382              Uruguay
2022-01-01                       1.479              Vanuatu
2022-01-01                       0.686               Zambia
2022-01-01                      -0.490             Zimbabwe

[8742 rows x 2 columns]

In [38]:
from statsmodels.tsa.arima.model import ARIMA
from sklearn.metrics import mean_squared_error
from math import sqrt

In [39]:
# Function to fit ARIMA model and make predictions for a country
def fit_arima(country_series):
    model = ARIMA(country_series, order=(5,1,0))  # Example ARIMA order
    model_fit = model.fit()
    predictions = model_fit.forecast(steps=5)  # Example forecasting 5 steps ahead
    return predictions

In [40]:
# Dictionary to store predictions for each country
predictions_dict = {}

# Loop through each country to fit the model and make predictions
for country, data in grouped:
    country_series = data['Surface Temperature Change']
    predictions = fit_arima(country_series)
    predictions_dict[country] = predictions

/opt/conda/lib/python3.10/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning:

No frequency information was provided, so inferred frequency YS-JAN will be used.

/opt/conda/lib/python3.10/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning:

No frequency information was provided, so inferred frequency YS-JAN will be used.

/opt/conda/lib/python3.10/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning:

No frequency information was provided, so inferred frequency YS-JAN will be used.

/opt/conda/lib/python3.10/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning:

No frequency information was provided, so inferred frequency YS-JAN will be used.

/opt/conda/lib/python3.10/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning:

No frequency information was provided, so inferred frequency YS-JAN will be used.

/opt/conda/lib/python3.10/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning:

No frequency informat

In [41]:
predictions_dict

{'Albania': 2023-01-01    1.544039
 2024-01-01    1.581766
 2025-01-01    1.556044
 2026-01-01    1.548471
 2027-01-01    1.551232
 Freq: YS-JAN, Name: predicted_mean, dtype: float64,
 'Algeria': 2023-01-01    1.779681
 2024-01-01    1.801337
 2025-01-01    1.833856
 2026-01-01    1.813483
 2027-01-01    1.836990
 Freq: YS-JAN, Name: predicted_mean, dtype: float64,
 'American Samoa': 2023-01-01    1.363247
 2024-01-01    1.339167
 2025-01-01    1.334091
 2026-01-01    1.332215
 2027-01-01    1.325819
 Freq: YS-JAN, Name: predicted_mean, dtype: float64,
 'Angola': 2023-01-01    1.417233
 2024-01-01    1.485208
 2025-01-01    1.256131
 2026-01-01    1.431289
 2027-01-01    1.365964
 Freq: YS-JAN, Name: predicted_mean, dtype: float64,
 'Antigua and Barbuda': 2023-01-01    0.913354
 2024-01-01    0.902140
 2025-01-01    0.858846
 2026-01-01    0.874159
 2027-01-01    0.882608
 Freq: YS-JAN, Name: predicted_mean, dtype: float64,
 'Argentina': 2023-01-01    0.904673
 2024-01-01    0.872355
 

In [42]:
 #Function to plot Surface Temperature Change for each country
def plot_countries():
    # Loop through each country in predictions_dict
    for country, predictions in predictions_dict.items():
        # Get the actual Surface Temperature Change data for the country
        actual_data = tsd[tsd['Country'] == country]['Surface Temperature Change']

        if actual_data.empty:
            print(f"No data found for {country}.")
            continue

        # Create a figure to hold the plot
        figxxi = go.Figure()

        # Plot the actual data
        figxxi.add_trace(go.Scatter(x=actual_data.index, y=actual_data.values,
                                 mode='lines+markers', name=f'Actual - {country}'))

        # Plot the predicted values if available
        if predictions is not None:
            # Extend the time index to include the future period
            future_index = pd.date_range(start=actual_data.index[-1], periods=len(predictions), freq='Y')
            # Plot the predicted values
            figxxi.add_trace(go.Scatter(x=future_index, y=predictions,
                                     mode='lines+markers', name=f'Predicted - {country}'))

        # Update layout
        figxxi.update_layout(title=f'Surface Temperature Change - Actual vs Predicted ({country})',
                          xaxis_title='Year',
                          yaxis_title='Surface Temperature Change')

        # Show the plot
        figxxi.show()

# Call the function to plot Surface Temperature Change for each country
plot_countries()